In [1]:
import folium
import pandas as pd
import geopandas as gpd

%load_ext watermark

In [2]:
%watermark -a "João Palmeiro" -u -d -v -p folium,pandas,geopandas

João Palmeiro 
last updated: 2020-03-22 

CPython 3.7.6
IPython 7.12.0

folium 0.10.1
pandas 1.0.1
geopandas 0.7.0


In [3]:
URL_GEOJSON = "https://raw.githubusercontent.com/joaopalmeiro/portugal-maps/master/geojson/ccdr_portugal_continental.geojson"
URL_DATA = "https://raw.githubusercontent.com/dssg-pt/covid19pt-data/master/data.csv"

In [4]:
df_map = gpd.read_file(URL_GEOJSON)

In [5]:
data = pd.read_csv(URL_DATA)

In [6]:
df_most_recent_date = data.tail(1)

In [7]:
confirmed_col = {
    "Alentejo": df_most_recent_date["confirmados_arsalentejo"].item(),
    "Algarve": df_most_recent_date["confirmados_arsalgarve"].item(),
    "Centro": df_most_recent_date["confirmados_arscentro"].item(),
    "Norte": df_most_recent_date["confirmados_arsnorte"].item(), 
    "RLVT": df_most_recent_date["confirmados_arslvt"].item()
}

In [8]:
df_map["confirmed"] = df_map["CCDR"].map(confirmed_col)

In [9]:
df_map

CCDR                                           geometry  confirmed
0  Alentejo  MULTIPOLYGON (((-8.18725 37.34111, -8.18728 37...          3
1   Algarve  MULTIPOLYGON (((-7.88042 36.97347, -7.88042 36...         31
2    Centro  MULTIPOLYGON (((-8.80879 39.48166, -8.80883 39...        137
3     Norte  MULTIPOLYGON (((-8.31622 40.78681, -8.31637 40...        644
4      RLVT  MULTIPOLYGON (((-8.76458 38.50812, -8.76458 38...        448

In [10]:
m = folium.Map(location=[39.557191, -7.8536599], zoom_start=6, tiles="cartodbpositron")

tooltip = folium.features.GeoJsonTooltip(
    fields=["CCDR", "confirmed"],
    aliases=["Regional Health Administration:", "Number of Confirmed Cases:"]
)

choropleth = folium.Choropleth(
    geo_data=df_map,
    name='choropleth',
    data=df_map[['CCDR', 'confirmed']],
    columns=['CCDR', 'confirmed'],
    key_on='feature.properties.CCDR',
    fill_color='Blues',
    fill_opacity=0.9,
    line_opacity=0.5,
    legend_name=f'Number of Confirmed Cases: {df_most_recent_date["data"].item()}'
).add_to(m)

choropleth.geojson.add_child(
    tooltip
)

folium.LayerControl('topleft').add_to(m)

m